# govdata mit SPARQL anfragen

https://rdflib.dev/sparqlwrapper/doc/1.8.5/main.html

In [2]:
#!pip install sparqlwrapper

## SELECT

SELECT gibt "Zeilen" einer Datenbank zurück.

In [3]:
from SPARQLWrapper import SPARQLWrapper, JSON, JSONLD, CSV, TURTLE
from rdflib import Graph

queryString_SELECT = """
SELECT * 
WHERE { ?s ?p ?o. }
LIMIT 3
"""

sparql_SELECT = SPARQLWrapper("https://www.govdata.de/sparql")
sparql_SELECT.setReturnFormat(CSV)
sparql_SELECT.setQuery(queryString_SELECT)


In [9]:
ret_SELECT = sparql_SELECT.query()
print(ret_SELECT)

SPARQLWrapper.Wrapper.QueryResult

In [5]:
results_SELECT = sparql_SELECT.query().convert()
results_SELECT

b's,p,o\r\nurn:uuid:a7eab660-7a93-506b-0ae0-12a7aeff289b,http://www.w3.org/1999/02/22-rdf-syntax-ns#type,http://www.w3.org/2006/vcard/ns#Organization\r\nurn:uuid:a7eab660-7a93-506b-0ae0-12a7aeff289b,http://www.w3.org/2006/vcard/ns#fn,GISAdminChemnitz\r\nurn:uuid:732b6cb7-ff7f-066b-d5e8-a0732695c0a3,http://www.w3.org/1999/02/22-rdf-syntax-ns#type,http://www.w3.org/2006/vcard/ns#Organization\r\n'

In [6]:
# alternativ query und convert in einem Rutsch
results_SELECT = sparql_SELECT.queryAndConvert()
results_SELECT

b's,p,o\r\nurn:uuid:a7eab660-7a93-506b-0ae0-12a7aeff289b,http://www.w3.org/1999/02/22-rdf-syntax-ns#type,http://www.w3.org/2006/vcard/ns#Organization\r\nurn:uuid:a7eab660-7a93-506b-0ae0-12a7aeff289b,http://www.w3.org/2006/vcard/ns#fn,GISAdminChemnitz\r\nurn:uuid:732b6cb7-ff7f-066b-d5e8-a0732695c0a3,http://www.w3.org/1999/02/22-rdf-syntax-ns#type,http://www.w3.org/2006/vcard/ns#Organization\r\n'

## CONSTRUCT

CONSTRUCT gibt einen Graphen zurück. Für uns die sauberere Version, da wir in der Graphenwelt bleiben, und insbesondere auch den Rückgabe-Graphen mit SPARQL weiter anfragen können. 

In [7]:
queryString_CONSTRUCT = """
CONSTRUCT { ?s ?p ?o. } 
WHERE { ?s ?p ?o. }
LIMIT 3
"""

sparql_CONSTRUCT = SPARQLWrapper("https://www.govdata.de/sparql")
sparql_CONSTRUCT.setReturnFormat(JSONLD)
sparql_CONSTRUCT.setQuery(queryString_CONSTRUCT)

In [8]:
results_CONSTRUCT = sparql_CONSTRUCT.query().convert()
results_CONSTRUCT

<Graph identifier=N1a466e07c62b476a8757d661f96b9363 (<class 'rdflib.graph.ConjunctiveGraph'>)>

In [10]:
for row in results_CONSTRUCT:
    print(row)

(rdflib.term.URIRef('urn:uuid:a7eab660-7a93-506b-0ae0-12a7aeff289b'), rdflib.term.URIRef('http://www.w3.org/2006/vcard/ns#fn'), rdflib.term.Literal('GISAdminChemnitz', lang='de'))
(rdflib.term.URIRef('urn:uuid:732b6cb7-ff7f-066b-d5e8-a0732695c0a3'), rdflib.term.URIRef('http://www.w3.org/1999/02/22-rdf-syntax-ns#type'), rdflib.term.URIRef('http://www.w3.org/2006/vcard/ns#Organization'))
(rdflib.term.URIRef('urn:uuid:a7eab660-7a93-506b-0ae0-12a7aeff289b'), rdflib.term.URIRef('http://www.w3.org/1999/02/22-rdf-syntax-ns#type'), rdflib.term.URIRef('http://www.w3.org/2006/vcard/ns#Organization'))


## Anfrage zu "Abfall"

In [11]:
queryString_abfall = """PREFIX dcat: <http://www.w3.org/ns/dcat#>
PREFIX dct: <http://purl.org/dc/terms/> 
PREFIX dcatde: <http://dcat-ap.de/def/dcatde/>

CONSTRUCT {
?expression
  <#access> ?a_url . 
}

WHERE {
    ?expression a dcat:Dataset ;
        dcat:keyword "Abfall" .
    ?expression
        dcat:distribution ?manifestation . 
    ?manifestation
        dcat:accessURL ?a_url ; 
        dct:format <http://publications.europa.eu/resource/authority/file-type/CSV> .
}
LIMIT 10"""


In [12]:
sparql_abfall = SPARQLWrapper("https://www.govdata.de/sparql")
sparql_abfall.setReturnFormat(JSONLD)
sparql_abfall.setQuery(queryString_abfall)

results_abfall = sparql_abfall.queryAndConvert()
type(results_abfall), len(results_abfall)

(rdflib.graph.ConjunctiveGraph, 10)

In [13]:
for row in results_abfall:
    print(row)

(rdflib.term.URIRef('https://opendata.schleswig-holstein.de/dataset/a4f4433a-e7c7-3903-9644-b49ec0b70c42'), rdflib.term.URIRef('http://server/unset-base/#access'), rdflib.term.URIRef('https://www.kiel.de/opendata/kiel_umwelt_klima_abfall_in_tonnen.csv'))
(rdflib.term.URIRef('https://opendata.schleswig-holstein.de/dataset/89acc463-746c-4976-b276-1580cb924bfd'), rdflib.term.URIRef('http://server/unset-base/#access'), rdflib.term.URIRef('https://opendata.schleswig-holstein.de/dataset/89acc463-746c-4976-b276-1580cb924bfd/resource/9508bc2f-79af-4aed-8fd6-c43162ac2b63/download/2021_sh_abfall_bilanz.csv'))
(rdflib.term.URIRef('https://www.opendata-hro.de/dataset/efdcff26-4066-40ad-9c30-6b4d24b9024b'), rdflib.term.URIRef('http://server/unset-base/#access'), rdflib.term.URIRef('https://geo.sv.rostock.de/download/opendata/recyclinghoefe/recyclinghoefe.csv'))
(rdflib.term.URIRef('https://www.opendata-hro.de/dataset/934ec65d-398b-49d0-9833-9aa713c0ff87'), rdflib.term.URIRef('http://server/unset-ba